In [1]:
from __future__ import print_function
import argparse
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms
from torch.optim.lr_scheduler import StepLR

In [2]:
BATCH_SIZE = 12

transform=transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))
        ])

dataset1 = datasets.MNIST('/bigdata/mnist', train=True, download=True, transform=transform)
dataset2 = datasets.MNIST('/bigdata/mnist', train=False, transform=transform)

train_loader = torch.utils.data.DataLoader(dataset1, batch_size=BATCH_SIZE)
test_loader = torch.utils.data.DataLoader(dataset2, batch_size=BATCH_SIZE)


Failed to download (trying next):
HTTP Error 503: Service Unavailable



  0%|          | 0/9912422 [00:00<?, ?it/s]

Extracting /bigdata/mnist/MNIST/raw/train-images-idx3-ubyte.gz to /bigdata/mnist/MNIST/raw

Failed to download (trying next):
HTTP Error 503: Service Unavailable



  0%|          | 0/28881 [00:00<?, ?it/s]

Extracting /bigdata/mnist/MNIST/raw/train-labels-idx1-ubyte.gz to /bigdata/mnist/MNIST/raw



  0%|          | 0/1648877 [00:00<?, ?it/s]

Extracting /bigdata/mnist/MNIST/raw/t10k-images-idx3-ubyte.gz to /bigdata/mnist/MNIST/raw



  0%|          | 0/4542 [00:00<?, ?it/s]

Extracting /bigdata/mnist/MNIST/raw/t10k-labels-idx1-ubyte.gz to /bigdata/mnist/MNIST/raw

Processing...
Done!


/home/jetzeschuurman/gitProjects/phd/tddl/venv/lib/python3.8/site-packages/torchvision/datasets/mnist.py:502: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  /pytorch/torch/csrc/utils/tensor_numpy.cpp:143.)
  return torch.from_numpy(parsed.astype(m[2], copy=False)).view(*s)


In [3]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.conv1 = nn.Conv2d(1, 32, 3, 1)
        self.conv2 = nn.Conv2d(32, 64, 3, 1)
        self.dropout1 = nn.Dropout(0.25)
        self.dropout2 = nn.Dropout(0.5)
        self.fc1 = nn.Linear(9216, 128)
        self.fc2 = nn.Linear(128, 10)

    def forward(self, x):
        x = self.conv1(x)
        x = F.relu(x)
        x = self.conv2(x)
        x = F.relu(x)
        x = F.max_pool2d(x, 2)
        x = self.dropout1(x)
        x = torch.flatten(x, 1)
        x = self.fc1(x)
        x = F.relu(x)
        x = self.dropout2(x)
        x = self.fc2(x)
        output = F.log_softmax(x, dim=1)
        return output


In [9]:
def train(model, device, train_loader, optimizer, epoch):
    model.train()
    for batch_idx, (data, target) in enumerate(train_loader):
        data, target = data.to(device), target.to(device)
        optimizer.zero_grad()
        output = model(data)
        loss = F.nll_loss(output, target)
        loss.backward()
        optimizer.step()
        print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
            epoch, batch_idx * len(data), len(train_loader.dataset),
            100. * batch_idx / len(train_loader), loss.item()))

In [5]:
def test(model, device, test_loader):
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in test_loader:
            data, target = data.to(device), target.to(device)
            output = model(data)
            test_loss += F.nll_loss(output, target, reduction='sum').item()  # sum up batch loss
            pred = output.argmax(dim=1, keepdim=True)  # get the index of the max log-probability
            correct += pred.eq(target.view_as(pred)).sum().item()

    test_loss /= len(test_loader.dataset)

    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))

In [6]:
device = torch.device("cuda")

In [8]:
model = Net().to(device)

In [10]:
LR = 1.0
GAMMA = 0.7

optimizer = optim.Adadelta(model.parameters(), lr=LR)
scheduler = StepLR(optimizer, step_size=1, gamma=GAMMA)

In [11]:
EPOCHS = 14
for epoch in range(1, 14 + 1):
    train(model, device, train_loader, optimizer, epoch)
    test(model, device, test_loader)
    scheduler.step()

Train Epoch: 1 [0/60000 (0%)]	Loss: 2.255028
Train Epoch: 1 [12/60000 (0%)]	Loss: 2.799468
Train Epoch: 1 [24/60000 (0%)]	Loss: 2.321604
Train Epoch: 1 [36/60000 (0%)]	Loss: 2.306582
Train Epoch: 1 [48/60000 (0%)]	Loss: 2.181079
Train Epoch: 1 [60/60000 (0%)]	Loss: 2.154644
Train Epoch: 1 [72/60000 (0%)]	Loss: 1.932449
Train Epoch: 1 [84/60000 (0%)]	Loss: 1.850262
Train Epoch: 1 [96/60000 (0%)]	Loss: 1.951115
Train Epoch: 1 [108/60000 (0%)]	Loss: 1.644083
Train Epoch: 1 [120/60000 (0%)]	Loss: 1.559989
Train Epoch: 1 [132/60000 (0%)]	Loss: 2.175546
Train Epoch: 1 [144/60000 (0%)]	Loss: 1.807784
Train Epoch: 1 [156/60000 (0%)]	Loss: 1.254705
Train Epoch: 1 [168/60000 (0%)]	Loss: 1.860206
Train Epoch: 1 [180/60000 (0%)]	Loss: 1.350559
Train Epoch: 1 [192/60000 (0%)]	Loss: 1.494782
Train Epoch: 1 [204/60000 (0%)]	Loss: 0.806548
Train Epoch: 1 [216/60000 (0%)]	Loss: 1.312996
Train Epoch: 1 [228/60000 (0%)]	Loss: 1.328396
Train Epoch: 1 [240/60000 (0%)]	Loss: 1.742439
Train Epoch: 1 [252/600

In [ ]:
torch.save(model.state_dict(), "mnist_cnn.pt")